<div align=center>
		
<font size=5>
In the Name of God
<font/>
<p></p>
<br/>
<br/>
<font>
Sharif University of Technology - Departmenet of Computer Engineering
</font>
<p></p>
<font color=cyan>
Artifical Intelligence - Dr. SamiEe
</font>
<br/>
<br/>

<hr/>
<font color=cyan>
Reinforcment Learning Practical Assignment
</font>
</div>

<ul>
  <li>Some cell's outputs have not been deleted. you can use these to make sure your implementation is correct.</li>
</ul>

In this notebook you will use the [openai gym](https://www.gymlibrary.dev/) library to train agent in reinforcment learning environment. Our environment is a discrete-state env (and it is deterministic).
make sure to upload your model performance video alongside this notebook. We suggest running this notebook on google colab so that you wont face any package errors.

we will first install the necessary packages.

In [ ]:
%pip install gym==0.26
%pip install imageio imageio_ffmpeg
%pip install pygame
%pip install pyglet==1.5.1 
%apt install python-opengl
%apt install ffmpeg
%apt install xvfb
%pip install pyvirtualdisplay
%pip install 'gym[box2d]'

the functions below will be used to make a video of the model performance. It will start the environment and choose the best action based on the given Qtable.

In [5]:
from IPython.display import HTML
from base64 import b64encode
import imageio

## comment this part if your not using google colab
from pyvirtualdisplay import Display
virtual_display = Display(visible=0, size=(1400, 900))
virtual_display.start()
######################

def record_video_taxi_env(env, Qtable, out_directory, fps=1, random_action=False):
  images = []  
  done = False
  state, info = env.reset(seed=random.randint(0,500))
  img = env.render()
  images.append(img)
  while not done:
    # Take the action (index) that have the maximum expected future reward given that state
    action = np.random.randint(6)  if random_action else np.argmax(Qtable[state][:])
    state, reward, done, truncated, info = env.step(action)
    img = env.render()
    images.append(img)
  imageio.mimsave(out_directory, [np.array(img) for i, img in enumerate(images)], fps=fps)

def show_video(video_path, video_width = 500):
  video_file = open(video_path, "r+b").read()
  video_url = f"data:video/mp4;base64,{b64encode(video_file).decode()}"
  return HTML(f"""<video width={video_width} controls><source src="{video_url}"></video>""")

## Part I: Taxi Environment (35 + 10 Points)

In [1]:
import numpy as np
import gym
import random
from tqdm import tqdm

In this exercise, we want to solve the Taxi-v3 environment. It is an environment, where we have a taxi, a passenger and a destination. taxi should go to the passenger's location, pick it up and then reach to destination and drop the passenger.
Please read more about this environment [here](https://www.gymlibrary.dev/environments/toy_text/taxi/)

**Question**  
Create an environment with the name `env` and print the number of states and actions.

In [50]:
env = ...

500
6


Let's run a random policy in this environement to get a better understanding of it.

In [8]:
record_video_taxi_env(env, None, 'taxi_random.mp4', fps=10, random_action=True)
show_video('taxi_random.mp4', video_width = 600)

/Users/amirhossein/Documents/Programming/Linear_Algebra_Project/venv/lib/python3.10/site-packages/gym/utils/passive_env_checker.py:233: DeprecationWarning: `np.bool8` is a deprecated alias for `np.bool_`.  (Deprecated NumPy 1.24)
  if not isinstance(terminated, (bool, np.bool8)):
IMAGEIO FFMPEG_WRITER WARNING: input image is not divisible by macro_block_size=16, resizing from (550, 350) to (560, 352) to ensure video compatibility with most codecs and players. To prevent resizing, make your input image divisible by the macro_block_size or set the macro_block_size to 1 (risking incompatibility).


**Question**

Briefly describe the state space, action space, and reward function of this environment.

**Answer:**  


**Question**
 
Complete the code for `initialize_q_table` function. It should create a Q-table of size (state_space, action_space) and initializes it. You are free to use whichever initialization you want (a good starting point is to initialize it with all zeros)

In [9]:
def initialize_q_table(state_space, action_space):
    ...
    #TODO: complete the function

In [10]:
Qtable = ...
#TODO: initialize the Q table here

**Question**

Complete the code for `epsilon_greedy_policy` function. It should select the best action according to the current Q-function with probability $1-\varepsilon$ and select a random action with probability $\varepsilon$.

In [11]:
def epsilon_greedy_policy(Qtable, state, epsilon):
    ...


**Question**
You need to choose appropriate hyperparameters for the agent to learn.

In particular, you must find a suitable learning rate and exploration parameters. To facilitate exploration, a common practice is to start with a high exploration rate ($\varepsilon$) and gradually decrease it as the agent gets better. To implement this, you need to specify the starting exploration rate (`max_epsilon`), the final exploration rate (`min_epsilon`) and a decay rate which reduces the exploration rate after each update (see the `train` function below).

In [12]:
# Training parameters
n_training_episodes = ...  # Total training episodes
n_eval_episodes = ...
learning_rate = ...           # Learning rate

# Environment parameters
max_steps = ...               # Max steps per episode
gamma = ...                    # Discounting rate

# Exploration parameters
max_epsilon = ...           # Exploration probability at start
min_epsilon = ...              # Minimum exploration probability 
decay_rate = ...            # Exponential decay rate for exploration prob

**Question**

Complete the `train` function which updates `Qtable` using the Q-learning update rule.

In [13]:
def train(n_training_episodes, min_epsilon, max_epsilon, decay_rate, env, max_steps, Qtable):
    ...
    #TODO: Implement training loop


We are now ready to train our agent.

In [ ]:
Qtable_trained = ...

Now, we will evaluate our agent. You don't need to write any code, just run the following cells as they are.

In [15]:
def evaluate_agent(env, max_steps, n_eval_episodes, Q):
  """
  Evaluate the agent for ``n_eval_episodes`` episodes and returns average reward and std of reward.
  :param env: The evaluation environment
  :param n_eval_episodes: Number of episode to evaluate the agent
  :param Q: The Q-table
  """
  episode_rewards = []
  for episode in tqdm(range(n_eval_episodes)):
    state, info = env.reset()
    step = 0
    terminated = False
    total_rewards_ep = 0
    
    for step in range(max_steps):
      action = np.argmax(Q[state][:])
      new_state, reward, terminated, truncated, info = env.step(action)
      total_rewards_ep += reward
        
      if terminated:
        break
      state = new_state
    episode_rewards.append(total_rewards_ep)
  mean_reward = np.mean(episode_rewards)
  std_reward = np.std(episode_rewards)

  return mean_reward, std_reward

In [16]:
mean_reward, std_reward = evaluate_agent(env, max_steps, n_eval_episodes, Qtable_trained)
print(f"Mean_reward={mean_reward:.2f} +/- {std_reward:.2f}") # should be around 0.65

100%|██████████| 10000/10000 [00:00<00:00, 10967.77it/s]

Mean_reward=7.88 +/- 2.67


Now let's see how well our model is doing.

In [18]:
record_video_taxi_env(env, Qtable_trained, 'taxi_trained.mp4', fps=10)
show_video('taxi_trained.mp4', video_width = 600)

IMAGEIO FFMPEG_WRITER WARNING: input image is not divisible by macro_block_size=16, resizing from (550, 350) to (560, 352) to ensure video compatibility with most codecs and players. To prevent resizing, make your input image divisible by the macro_block_size or set the macro_block_size to 1 (risking incompatibility).


Next, we will take a look at the Q-function that was learned.

In [ ]:
print(Qtable_trained)

**Question**

Assume that `Qtable_trained` is the correct Q-function for the final epsilon-greedy policy that was used in training. What is the value function that corresponds to this policy? Write down the relation between $V_\pi$ and $Q_\pi$ and use it to complete the following code block.

**Answer:**


In [48]:
Vtable_trained = ...

Take a look at the value function

In [ ]:
print(Vtable_trained)

**Question**  
Write a function to generate a visualization for the value function using a heatmap. In a few words, explain what you see.

In [47]:
import matplotlib.pyplot as plt


def visualize(Vtable):
  """
  Visualize the value function
  :param Vtable: The value function
  """
  ...

**Question**  
Can we use a pure greedy policy for Q-learning? Explain.